In [1]:
import torch
from torch import nn
from torch.utils.data import DataLoader
from torch.utils.data import Dataset
from torchvision import transforms
from torch.nn.functional import one_hot
from matplotlib import pyplot as plt
import json

In [2]:
f = open('dataset2.json','r')
s = f.read()
f.close()
data = json.loads(s)

In [3]:
data

[{'data': [[0, 0],
   [1, 1],
   [0, 1],
   [1, 1],
   [0, 1],
   [1, 1],
   [0, 1],
   [1, 2],
   [1, 2],
   [1, 2],
   [1, 2],
   [0, 2],
   [2, 2],
   [1, 3],
   [1, 3],
   [1, 4],
   [2, 3],
   [1, 4],
   [2, 5],
   [1, 3],
   [2, 5],
   [1, 4],
   [2, 6],
   [2, 4],
   [1, 4],
   [3, 7],
   [1, 6],
   [2, 7],
   [2, 5],
   [2, 5],
   [2, 8],
   [1, 4],
   [3, 9],
   [2, 7],
   [2, 6],
   [2, 7],
   [1, 6],
   [2, 7],
   [2, 6],
   [1, 5],
   [3, 9],
   [1, 5],
   [1, 5],
   [2, 8],
   [2, 5],
   [2, 8],
   [1, 6],
   [1, 4],
   [1, 7],
   [2, 6],
   [1, 5],
   [1, 6],
   [1, 7],
   [1, 4],
   [1, 5],
   [2, 6],
   [1, 5],
   [0, 4],
   [1, 5],
   [1, 5],
   [1, 3],
   [1, 6],
   [1, 4],
   [0, 3],
   [1, 4],
   [1, 5],
   [1, 5],
   [1, 3],
   [1, 4],
   [1, 3],
   [1, 4],
   [0, 3],
   [1, 3],
   [1, 2],
   [1, 3],
   [1, 4],
   [1, 2],
   [1, 3],
   [1, 2],
   [1, 3],
   [1, 2],
   [0, 1],
   [1, 3],
   [1, 1],
   [2, 2],
   [0, 2],
   [1, 1],
   [1, 1],
   [0, 1],
   [1, 1],
  

In [4]:
class MouseData(Dataset):
    def __init__(self, data):
        self.data = data

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        x = torch.FloatTensor(self.data[index]['data'])
        y = torch.zeros(26)
        y[ord(self.data[index]['letter'])-97]=1
        # Process the sample as needed and return it
        return x,y

In [5]:
df = MouseData(data)

In [6]:
df.__getitem__(1)

(tensor([[ 0.,  0.],
         [ 0.,  1.],
         [ 0.,  1.],
         [ 0.,  2.],
         [ 0.,  1.],
         [ 0.,  3.],
         [ 1.,  2.],
         [ 0.,  3.],
         [ 1.,  2.],
         [ 0.,  3.],
         [ 1.,  3.],
         [ 1.,  4.],
         [ 1.,  3.],
         [ 1.,  5.],
         [ 0.,  5.],
         [ 1.,  4.],
         [ 1.,  5.],
         [ 1.,  4.],
         [ 1.,  7.],
         [ 1.,  4.],
         [ 1.,  7.],
         [ 1.,  5.],
         [ 1.,  7.],
         [ 1.,  6.],
         [ 1.,  8.],
         [ 1.,  5.],
         [ 1.,  8.],
         [ 1.,  8.],
         [ 1.,  7.],
         [ 1.,  7.],
         [ 1.,  8.],
         [ 1.,  7.],
         [ 1.,  7.],
         [ 1.,  9.],
         [ 1.,  6.],
         [ 1.,  8.],
         [ 1.,  7.],
         [ 1.,  8.],
         [ 0.,  5.],
         [ 1.,  9.],
         [ 1.,  8.],
         [ 1.,  7.],
         [ 1.,  6.],
         [ 1.,  5.],
         [ 1.,  8.],
         [ 1.,  8.],
         [ 2.,  6.],
         [ 1.

In [7]:
class clf(nn.Module):
    def __init__(self, input_size, hidden_size, num_classes):
        super(clf, self).__init__()
        self.hidden_size = hidden_size
        self.lstm = nn.LSTM(input_size, hidden_size, batch_first=True)
        self.fc = nn.Linear(hidden_size, num_classes)
    
    def forward(self, x):
        # Initialize the hidden and cell states
        h0 = torch.zeros(1, x.size(0), self.hidden_size).to(x.device)
        c0 = torch.zeros(1, x.size(0), self.hidden_size).to(x.device)
        
        # Forward propagate through the LSTM layer
        out, _ = self.lstm(x, (h0, c0))
        
        # Reshape the output of the last LSTM step for classification
        out = out[:, -1, :]
        
        # Pass the output through the fully connected layer
        out = self.fc(out)
        
        return out

In [8]:
model = clf(2,256,26)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)

In [9]:
batch_size = 1
dataloader = torch.utils.data.DataLoader(df, batch_size=batch_size, shuffle=True)

In [10]:
next(enumerate(dataloader))

(0,
 [tensor([[[ 0.,  0.],
           [ 0., -1.],
           [ 0., -1.],
           [ 1., -1.],
           [ 0., -2.],
           [ 0., -1.],
           [ 0., -2.],
           [ 1., -2.],
           [ 0., -1.],
           [ 1., -1.],
           [ 0., -3.],
           [ 0., -2.],
           [ 1., -3.],
           [ 1., -2.],
           [ 0., -3.],
           [ 1., -3.],
           [ 1., -3.],
           [ 1., -3.],
           [ 0., -3.],
           [ 1., -3.],
           [ 1., -4.],
           [ 0., -4.],
           [ 1., -3.],
           [ 1., -3.],
           [ 1., -4.],
           [ 0., -3.],
           [ 1., -6.],
           [ 1., -4.],
           [ 1., -4.],
           [ 0., -5.],
           [ 1., -3.],
           [ 1., -6.],
           [ 1., -5.],
           [ 0., -3.],
           [ 1., -6.],
           [ 0., -4.],
           [ 1., -4.],
           [ 0., -5.],
           [ 1., -5.],
           [ 0., -4.],
           [ 0., -6.],
           [ 1., -5.],
           [ 0., -4.],
       

In [11]:
num_epochs = 30
for epoch in range(num_epochs):
    mean = []
    for x, y in dataloader:  # Iterate over the training dataset
        optimizer.zero_grad()  # Zero the gradients
        outputs = model(x)  # Forward pass
        loss = criterion(outputs, y)  # Compute the loss
        loss.backward()  # Backward pass
        optimizer.step()  # Update the model parameters
        if(epoch == 10):
            for g in optimizer.param_groups:
                g['lr'] = 0.0005
        if(epoch == 15):
            for g in optimizer.param_groups:
                g['lr'] = 0.0001
        
    mean.append(loss.item())
    print( "Epoch:",epoch, "loss:", torch.mean(torch.FloatTensor(mean)).item())

Epoch: 0 loss: 2.8771650791168213
Epoch: 1 loss: 1.6445839405059814
Epoch: 2 loss: 2.1278676986694336
Epoch: 3 loss: 1.776038646697998
Epoch: 4 loss: 0.6788747310638428
Epoch: 5 loss: 1.8120348453521729
Epoch: 6 loss: 1.4423969984054565
Epoch: 7 loss: 1.3041843175888062
Epoch: 8 loss: 0.3998457193374634
Epoch: 9 loss: 0.1729184091091156
Epoch: 10 loss: 1.2776254415512085
Epoch: 11 loss: 0.9129617810249329
Epoch: 12 loss: 0.5850989818572998
Epoch: 13 loss: 0.5531595945358276
Epoch: 14 loss: 1.0221810340881348
Epoch: 15 loss: 0.06849515438079834
Epoch: 16 loss: 0.343515545129776
Epoch: 17 loss: 0.13651791214942932
Epoch: 18 loss: 0.13325142860412598
Epoch: 19 loss: 0.6523590087890625
Epoch: 20 loss: 0.290321946144104
Epoch: 21 loss: 0.011218918487429619
Epoch: 22 loss: 0.5992280840873718
Epoch: 23 loss: 0.18460066616535187
Epoch: 24 loss: 0.6722382307052612
Epoch: 25 loss: 0.8544815182685852
Epoch: 26 loss: 0.05914432182908058
Epoch: 27 loss: 0.12265438586473465
Epoch: 28 loss: 0.0921708

In [12]:
a = torch.FloatTensor(
    [[0, 0], [-1, 0], [-1, 0], [-1, 1], [-1, 0], [-2, 1], [-1, 0], [-1, 1], [-2, 0], [-2, 1], [-1, 0], [-2, 1], [-2, 1], [-3, 1], [-3, 1], [-3, 0], [-2, 1], [-3, 1], [-3, 1], [-3, 1], [-3, 1], [-3, 1], [-3, 1], [-4, 1], [-4, 1], [-4, 1], [-3, 1], [-5, 1], [-3, 1], [-4, 1], [-3, 0], [-5, 2], [-3, 0], [-4, 1], [-4, 0], [-4, 1], [-4, 0], [-5, 1], [-3, 0], [-4, 1], [-4, 0], [-4, 0], [-3, 0], [-4, 0], [-3, 0], [-2, 0], [-4, 0], [-3, 0], [-3, 0], [-2, 0], [-2, 0], [-3, 0], [-2, -1], [-2, 0], [-2, -1], [-2, -1], [-1, -1], [-2, -1], [-1, -1], [-2, -1], [-1, -1], [-2, -1], [-1, -1], [-1, -1], [-1, -2], [-2, -1], [-1, -2], [-1, -1], [-1, -2], [-1, -1], [-1, -2], [0, -1], [-1, -2], [0, -2], [-1, -2], [0, -2], [-1, -2], [0, -2], [0, -2], [0, -3], [0, -2], [0, -2], [0, -3], [0, -3], [0, -2], [1, -2], [0, -3], [1, -2], [1, -3], [1, -3], [1, -3], [1, -2], [1, -2], [1, -3], [1, -2], [2, -2], [1, -2], [2, -3], [2, -2], [2, -2], [1, -2], [2, -2], [1, -1], [2, -2], [2, -1], [2, -1], [2, -1], [2, -1], [2, 0], [2, -1], [2, 0], [2, 0], [2, 0], [3, 0], [3, 0], [2, 1], [3, 1], [2, 1], [3, 2], [3, 1], [3, 2], [3, 2], [2, 2], [4, 3], [3, 2], [3, 4], [3, 3], [3, 2], [3, 3], [3, 4], [3, 3], [3, 4], [3, 3], [3, 4], [3, 3], [3, 4], [3, 3], [3, 4], [2, 4], [2, 3], [3, 5], [2, 2], [3, 5], [2, 3], [1, 3], [2, 3], [2, 5], [2, 3], [1, 3], [1, 3], [1, 2], [1, 3], [1, 3], [0, 2], [1, 2], [1, 2], [0, 2], [0, 1], [0, 2], [0, 1], [0, 1], [0, 1], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, -1], [-2, -1], [0, -1], [-1, -1], [-2, -1], [-1, -1], [-1, -1], [-1, -1], [-1, -1], [-1, -2], [-2, -2], [-1, -1], [-1, -2], [-1, -2], [-2, -2], [-1, -1], [-1, -3], [-2, -2], [0, -2], [-2, -2], [-1, -4], [-2, -3], [-1, -3], [-1, -3], [-1, -2], [-1, -4], [-1, -3], [0, -3], [-1, -4], [-1, -4], [-1, -4], [0, -4], [0, -3], [-1, -4], [0, -4], [0, -4], [0, -6], [0, -3], [0, -5], [0, -5], [0, -4], [0, -4], [1, -5], [1, -4], [0, -4], [1, -5], [1, -4], [1, -4], [1, -5], [1, -4], [2, -4], [1, -6], [2, -4], [1, -3], [2, -4], [2, -4], [2, -4], [2, -3], [1, -2], [2, -3], [3, -4], [2, -3], [2, -3], [2, -2], [2, -2], [4, -3], [2, -2], [2, -2], [2, -2], [3, -1], [2, -2], [2, -1], [3, -1], [2, -2], [3, -1], [2, -1], [2, 0], [2, -1], [2, -1], [3, -1], [2, -1], [1, 0], [2, 0], [2, -1], [1, 0], [2, -1], [2, 0], [1, 0], [1, -1], [1, 0], [2, 0], [1, 0], [1, 0], [1, 0], [1, 0], [1, -1], [1, 0], [2, 0], [1, 0], [1, 0], [1, 0], [1, 0], [1, 0], [1, 0], [1, 1], [1, 0], [1, 1], [1, 0], [0, 1], [1, 0], [1, 1], [1, 1], [1, 1], [1, 1], [0, 1], [1, 0], [0, 1], [1, 0], [0, 1], [0, 0]]
)

In [13]:
a.shape

torch.Size([286, 2])

In [14]:
torch.argmax(model(a.view(1,a.shape[0],2)))

tensor(2)

In [15]:
torch.save(model.state_dict(), 'model.pt')